In [59]:
import pandas as pd
import xlrd
import os 
import datetime
import folium 
import plotly.express as px
import plotly
import plotly.graph_objects as go
import argparse
import pyarrow
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from plotly.subplots import make_subplots
import plotly.figure_factory as ff
from functools import reduce
import numpy as np

In [2]:
folder_path = "/Users/ruiwenzhang/Dropbox/PSV Rider Feedback/Data/Sensor Data/FinalData"
outputs_path = "/Users/ruiwenzhang/Desktop/Kenya/Weekly_report"
if not os.path.exists(outputs_path):
                os.mkdir(outputs_path)
eco_data_path = os.path.join(folder_path, "echodriving.gz.parquet")

In [3]:
eco_data_raw = pd.read_parquet(eco_data_path)
eco_data_raw

violation            begin_datetime  latitude_begin  \
0             Brake: extreme 2021-07-01 05:14:45+03:00       -0.693320   
1               Turn: medium 2021-07-01 08:00:47+03:00       -0.627922   
2              Brake: medium 2021-07-01 08:18:56+03:00       -0.641155   
3             Brake: extreme 2021-07-01 08:33:04+03:00       -0.674540   
4              Turn: extreme 2021-07-01 08:40:59+03:00       -0.710713   
...                      ...                       ...             ...   
26486  Acceleration: extreme 2021-08-10 14:25:29+03:00       -0.517383   
26487   Acceleration: medium 2021-08-10 14:32:00+03:00       -0.501545   
26488          Brake: medium 2021-08-10 14:33:49+03:00       -0.494955   
26489         Brake: extreme 2021-08-10 17:40:24+03:00       -0.452647   
26490  Acceleration: extreme 2021-08-10 19:28:16+03:00       -0.461387   

       longitude_begin              end_datetime  latitude_end  longitude_end  \
0            37.340107 2021-07-01 05:14:45+03:00     -0.693368      37.340037   
1            37.022110 2021-07-01 08:00:48+03:00     -0.627978      37.022003   
2            37.082898 2021-07-01 08:18:57+03:00     -0.641157      37.082925   
3            37.116143 2021-07-01 08:33:04+03:00     -0.674595      37.116137   
4            37.153908 2021-07-01 08:40:59+03:00     -0.710785      37.153978   
...                ...                       ...           ...            ...   
26486        36.940903 2021-08-10 14:25:29+03:00     -0.517332      36.940887   
26487        36.938907 2021-08-10 14:32:00+03:00     -0.501545      36.938920   
26488        36.940573 2021-08-10 14:33:49+03:00     -0.494922      36.940643   
26489        36.958742 2021-08-10 17:40:24+03:00     -0.452693      36.958710   
26490        36.943023 2021-08-10 19:28:16+03:00     -0.461353      36.943063   

       value_g  max_speed_kmhr time_interval  distance_km  reg_no_id  \
0         0.40            34.0       0:00:00         14.0   23672019   
1         0.34            35.0       0:00:01         49.0   23457115   
2         0.32             8.0       0:00:01         57.0   23457115   
3         0.40            18.0       0:00:00         63.0   23457115   
4         0.41            45.0       0:00:00         70.0   23457115   
...        ...             ...           ...          ...        ...   
26486     0.40            21.0       0:00:00         34.0   23146908   
26487     0.32            14.0       0:00:00         37.0   23146908   
26488     0.32            26.0       0:00:00         38.0   23146908   
26489     0.40            21.0       0:00:00         59.0   23146908   
26490     0.40            24.0       0:00:00         86.0   23146908   

               reg_no  
0      hiace kcf 954t  
1      hiace kcw 543m  
2      hiace kcw 543m  
3      hiace kcw 543m  
4      hiace kcw 543m  
...               ...  
26486  hiace kcl 589a  
26487  hiace kcl 589a  
26488  hiace kcl 589a  
26489  hiace kcl 589a  
26490  hiace kcl 589a  

[26491 rows x 13 columns]

In [4]:
def data_process_eco(df):
    #df.Beginning = pd.to_datetime(df.Beginning.str.replace(".","-"), format = "%d-%m-%Y %H:%M:%S")
    df["begin_date"] = df.begin_datetime.dt.date
    df["begin_hour"] = df.begin_datetime.dt.hour
    #df.End = pd.to_datetime(df.End.str.replace(".","-"), format = "%d-%m-%Y %H:%M:%S")
    df["end_date"] = df.end_datetime.dt.date
    df["end_hour"] = df.end_datetime.dt.hour
    df["harsh_event"] = df.violation.str.split(" ", expand=True)[0]
    df["level"] = df.violation.str.split(" ", expand=True)[1]
   
    
    
    return df

In [5]:
eco_data = data_process_eco(eco_data_raw)
eco_data

violation            begin_datetime  latitude_begin  \
0             Brake: extreme 2021-07-01 05:14:45+03:00       -0.693320   
1               Turn: medium 2021-07-01 08:00:47+03:00       -0.627922   
2              Brake: medium 2021-07-01 08:18:56+03:00       -0.641155   
3             Brake: extreme 2021-07-01 08:33:04+03:00       -0.674540   
4              Turn: extreme 2021-07-01 08:40:59+03:00       -0.710713   
...                      ...                       ...             ...   
26486  Acceleration: extreme 2021-08-10 14:25:29+03:00       -0.517383   
26487   Acceleration: medium 2021-08-10 14:32:00+03:00       -0.501545   
26488          Brake: medium 2021-08-10 14:33:49+03:00       -0.494955   
26489         Brake: extreme 2021-08-10 17:40:24+03:00       -0.452647   
26490  Acceleration: extreme 2021-08-10 19:28:16+03:00       -0.461387   

       longitude_begin              end_datetime  latitude_end  longitude_end  \
0            37.340107 2021-07-01 05:14:45+03:00     -0.693368      37.340037   
1            37.022110 2021-07-01 08:00:48+03:00     -0.627978      37.022003   
2            37.082898 2021-07-01 08:18:57+03:00     -0.641157      37.082925   
3            37.116143 2021-07-01 08:33:04+03:00     -0.674595      37.116137   
4            37.153908 2021-07-01 08:40:59+03:00     -0.710785      37.153978   
...                ...                       ...           ...            ...   
26486        36.940903 2021-08-10 14:25:29+03:00     -0.517332      36.940887   
26487        36.938907 2021-08-10 14:32:00+03:00     -0.501545      36.938920   
26488        36.940573 2021-08-10 14:33:49+03:00     -0.494922      36.940643   
26489        36.958742 2021-08-10 17:40:24+03:00     -0.452693      36.958710   
26490        36.943023 2021-08-10 19:28:16+03:00     -0.461353      36.943063   

       value_g  max_speed_kmhr time_interval  distance_km  reg_no_id  \
0         0.40            34.0       0:00:00         14.0   23672019   
1         0.34            35.0       0:00:01         49.0   23457115   
2         0.32             8.0       0:00:01         57.0   23457115   
3         0.40            18.0       0:00:00         63.0   23457115   
4         0.41            45.0       0:00:00         70.0   23457115   
...        ...             ...           ...          ...        ...   
26486     0.40            21.0       0:00:00         34.0   23146908   
26487     0.32            14.0       0:00:00         37.0   23146908   
26488     0.32            26.0       0:00:00         38.0   23146908   
26489     0.40            21.0       0:00:00         59.0   23146908   
26490     0.40            24.0       0:00:00         86.0   23146908   

               reg_no  begin_date  begin_hour    end_date  end_hour  \
0      hiace kcf 954t  2021-07-01           5  2021-07-01         5   
1      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
2      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
3      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
4      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
...               ...         ...         ...         ...       ...   
26486  hiace kcl 589a  2021-08-10          14  2021-08-10        14   
26487  hiace kcl 589a  2021-08-10          14  2021-08-10        14   
26488  hiace kcl 589a  2021-08-10          14  2021-08-10        14   
26489  hiace kcl 589a  2021-08-10          17  2021-08-10        17   
26490  hiace kcl 589a  2021-08-10          19  2021-08-10        19   

         harsh_event    level  
0             Brake:  extreme  
1              Turn:   medium  
2             Brake:   medium  
3             Brake:  extreme  
4              Turn:  extreme  
...              ...      ...  
26486  Acceleration:  extreme  
26487  Acceleration:   medium  
26488         Brake:   medium  
26489         Brake:  extreme  
26490  Acceleration:  extreme  

[26491 rows x 19 columns]

In [81]:
def boxplot(df,export = True, show = True):
    fig = make_subplots(rows = 1, cols = 3)
    
    fig.add_trace(go.Box(
    y = df.value_g.values,
    name='Acceleration value',
    marker_color='#FF851B',
    boxpoints='suspectedoutliers'), row=1, col=1)
    
    fig.add_trace(go.Box(
    y = df.max_speed_kmhr.values,
    name='Max speed',
    marker_color= '#3D9970',
    boxpoints='suspectedoutliers'), row=1, col=2)
    
    fig.add_trace(go.Box(
    y = df.distance_km.values,
    name='Distance km',
    marker_color= '#FF4136',
    boxpoints='suspectedoutliers'), row=1, col=3)
    
    fig.update_layout(title_text="Boxplot of Max Speed & Acceleration Value & Distance")
    
    if export:
            file_name = outputs_path + '/' + 'boxplots_eco_driving2.html'
            print('Saving: ' + file_name)
            plotly.offline.plot(fig, filename = file_name, auto_open=False)
    if show:
            fig.show()

In [77]:
boxplot(eco_data)

Saving: /Users/ruiwenzhang/Desktop/Kenya/Weekly_report/boxplots_eco_driving.html


#### without speeding

In [79]:
drop_rows = (eco_data.violation.str.startswith('Speeding'))
eco_data2 = eco_data[~drop_rows]

In [82]:
boxplot(eco_data2)

Saving: /Users/ruiwenzhang/Desktop/Kenya/Weekly_report/boxplots_eco_driving2.html


In [95]:
dist_neg = eco_data2[eco_data2['distance_km'] < 0]
dist_neg.groupby('violation').apply(lambda x: pd.Series({
    'count':x['reg_no'].count()
})).reset_index()

violation  count
0          Brake: extreme      4
1            Turn: medium      4
2           Brake: medium      5
3           Turn: extreme      1
4   Acceleration: extreme      4
5    Acceleration: medium      7
6                 Braking    297
7            Acceleration    169
8                    Turn    129
9           Harsh driving      1
10         Speeding: mild      0
11       Speeding: medium      0
12      Speeding: extreme      0

In [98]:
#dist_out = eco_data2[eco_data2['distance_km'] > 622]
#dist_out.groupby('violation').apply(lambda x: pd.Series({
#    'count':x['reg_no'].count()
#})).reset_index()

#### Distribution of the max speed at hourly level by vehicle

In [85]:
summary_harshspd_hr = eco_data2.groupby(["reg_no_id","reg_no","begin_date", "begin_hour"]).apply(lambda x: pd.Series({
    "min": x["max_speed_kmhr"].min(), "25%": x["max_speed_kmhr"].quantile(0.25),
    "50%": x["max_speed_kmhr"].quantile(0.5), 'avg': x["max_speed_kmhr"].mean(), "75%": x["max_speed_kmhr"].quantile(0.75), 
    "90%": x["max_speed_kmhr"].quantile(0.9), "max": x["max_speed_kmhr"].max()})).reset_index()
summary_harshspd_hr

reg_no_id             reg_no  begin_date  begin_hour   min   25%   50%  \
0      23146908     hiace kcl 589a  2021-07-01          12   3.0   3.0   3.0   
1      23146908     hiace kcl 589a  2021-07-07          13  19.0  19.0  19.0   
2      23146908     hiace kcl 589a  2021-07-07          14  25.0  25.0  25.0   
3      23146908     hiace kcl 589a  2021-07-07          17  11.0  14.0  17.0   
4      23146908     hiace kcl 589a  2021-07-08           9  47.0  47.0  47.0   
...         ...                ...         ...         ...   ...   ...   ...   
2950   23672039  sprinter kch 471d  2021-08-09           8   5.0   5.0   5.0   
2951   23672039  sprinter kch 471d  2021-08-09          13  35.0  35.0  35.0   
2952   23869847     hiace kct 045g  2021-08-06          17  97.0  97.0  97.0   
2953   23869847     hiace kct 045g  2021-08-08          11  49.0  49.0  49.0   
2954   23869847     hiace kct 045g  2021-08-09          11  32.0  32.0  32.0   

            avg   75%   90%   max  
0      3.000000   3.0   3.0   3.0  
1     19.000000  19.0  19.0  19.0  
2     25.000000  25.0  25.0  25.0  
3     16.333333  19.0  20.2  21.0  
4     47.000000  47.0  47.0  47.0  
...         ...   ...   ...   ...  
2950   5.000000   5.0   5.0   5.0  
2951  35.000000  35.0  35.0  35.0  
2952  97.000000  97.0  97.0  97.0  
2953  49.000000  49.0  49.0  49.0  
2954  32.000000  32.0  32.0  32.0  

[2955 rows x 11 columns]

#### Distribution of max speed & acc & distance by violation types

In [99]:
hs_range = eco_data2.groupby(["violation"]).apply(lambda x: pd.Series({
    "count": x["reg_no_id"].count(), 
    "min_maxsp": x["max_speed_kmhr"].min(), 
    "maxsp25%": x["max_speed_kmhr"].quantile(0.25),"maxsp50%": x["max_speed_kmhr"].quantile(0.5), 
    'maxspavg': x["max_speed_kmhr"].mean(), "maxsp75%": x["max_speed_kmhr"].quantile(0.75), 
    "maxsp90%": x["max_speed_kmhr"].quantile(0.9),"max_maxsp": x["max_speed_kmhr"].max(),
    "min_acc": x["value_g"].min(), "acc25%": x["value_g"].quantile(0.25),
    "acc50%": x["value_g"].quantile(0.5), 'accavg': x["value_g"].mean(), "acc75%": x["value_g"].quantile(0.75), 
    "acc90%": x["value_g"].quantile(0.9),"max_acc": x["value_g"].max()
    #"min_dis": x["distance_km"].min(), "dis25%": x["distance_km"].quantile(0.25),
    #"dis50%": x["distance_km"].quantile(0.5), 'disavg': x["distance_km"].mean(), "dis75%": x["distance_km"].quantile(0.75), 
    #"dis90%": x["distance_km"].quantile(0.9),"max_dis": x["distance_km"].max()
})).reset_index()
hs_range

violation    count  min_maxsp  maxsp25%  maxsp50%   maxspavg  \
0          Brake: extreme   2489.0        0.0      22.0      32.0  34.256328   
1            Turn: medium    613.0        7.0      43.0      59.0  58.156607   
2           Brake: medium    686.0        0.0      18.0      27.0  29.747813   
3           Turn: extreme    304.0        6.0      40.0      51.0  53.996711   
4   Acceleration: extreme   1324.0       10.0      30.0      42.0  43.697130   
5    Acceleration: medium    465.0        8.0      23.0      36.0  40.870968   
6                 Braking  11408.0        0.0      20.0      34.0  36.202665   
7            Acceleration   4389.0        4.0      24.0      33.0  36.255411   
8                    Turn   4585.0        0.0      39.0      59.0  56.789749   
9           Harsh driving    175.0       10.0      28.0      37.0  39.982857   
10         Speeding: mild      0.0        NaN       NaN       NaN        NaN   
11       Speeding: medium      0.0        NaN       NaN       NaN        NaN   
12      Speeding: extreme      0.0        NaN       NaN       NaN        NaN   

    maxsp75%  maxsp90%  max_maxsp  min_acc  acc25%  acc50%    accavg  acc75%  \
0      45.00      57.0      114.0     0.35    0.40   0.400  0.449892  0.4900   
1      72.00      84.0      121.0     0.31    0.32   0.340  0.344241  0.3600   
2      39.00      51.0       94.0     0.31    0.32   0.320  0.323397  0.3300   
3      65.25      80.0      109.0     0.40    0.43   0.475  0.541414  0.5825   
4      54.00      68.0      124.0     0.40    0.40   0.450  0.494517  0.5300   
5      55.00      72.6      116.0     0.32    0.33   0.360  0.348667  0.3600   
6      50.00      65.0      114.0     0.10    0.12   0.140  0.158708  0.1700   
7      44.00      61.0      111.0     0.10    0.10   0.120  0.153420  0.1500   
8      74.00      87.0      134.0     0.10    0.11   0.130  0.151466  0.1700   
9      48.00      67.6      104.0     0.30    0.57   0.620  0.614171  0.6800   
10       NaN       NaN        NaN      NaN     NaN     NaN       NaN     NaN   
11       NaN       NaN        NaN      NaN     NaN     NaN       NaN     NaN   
12       NaN       NaN        NaN      NaN     NaN     NaN       NaN     NaN   

    acc90%  max_acc  
0    0.570     2.02  
1    0.380     0.40  
2    0.330     0.35  
3    0.754     3.15  
4    0.610     1.32  
5    0.360     0.40  
6    0.220     1.34  
7    0.220     0.93  
8    0.220     1.69  
9    0.790     1.19  
10     NaN      NaN  
11     NaN      NaN  
12     NaN      NaN

### plot the range of acceleration value, maxspeed and distance for each violation type across all the vehicles 

In [7]:
drop_rows = (eco_data.violation.str.startswith('Speeding') | eco_data.violation.str.startswith('Harsh'))
eco_data_reprt = eco_data[~drop_rows]
eco_data_reprt

violation            begin_datetime  latitude_begin  \
0             Brake: extreme 2021-07-01 05:14:45+03:00       -0.693320   
1               Turn: medium 2021-07-01 08:00:47+03:00       -0.627922   
2              Brake: medium 2021-07-01 08:18:56+03:00       -0.641155   
3             Brake: extreme 2021-07-01 08:33:04+03:00       -0.674540   
4              Turn: extreme 2021-07-01 08:40:59+03:00       -0.710713   
...                      ...                       ...             ...   
26486  Acceleration: extreme 2021-08-10 14:25:29+03:00       -0.517383   
26487   Acceleration: medium 2021-08-10 14:32:00+03:00       -0.501545   
26488          Brake: medium 2021-08-10 14:33:49+03:00       -0.494955   
26489         Brake: extreme 2021-08-10 17:40:24+03:00       -0.452647   
26490  Acceleration: extreme 2021-08-10 19:28:16+03:00       -0.461387   

       longitude_begin              end_datetime  latitude_end  longitude_end  \
0            37.340107 2021-07-01 05:14:45+03:00     -0.693368      37.340037   
1            37.022110 2021-07-01 08:00:48+03:00     -0.627978      37.022003   
2            37.082898 2021-07-01 08:18:57+03:00     -0.641157      37.082925   
3            37.116143 2021-07-01 08:33:04+03:00     -0.674595      37.116137   
4            37.153908 2021-07-01 08:40:59+03:00     -0.710785      37.153978   
...                ...                       ...           ...            ...   
26486        36.940903 2021-08-10 14:25:29+03:00     -0.517332      36.940887   
26487        36.938907 2021-08-10 14:32:00+03:00     -0.501545      36.938920   
26488        36.940573 2021-08-10 14:33:49+03:00     -0.494922      36.940643   
26489        36.958742 2021-08-10 17:40:24+03:00     -0.452693      36.958710   
26490        36.943023 2021-08-10 19:28:16+03:00     -0.461353      36.943063   

       value_g  max_speed_kmhr time_interval  distance_km  reg_no_id  \
0         0.40            34.0       0:00:00         14.0   23672019   
1         0.34            35.0       0:00:01         49.0   23457115   
2         0.32             8.0       0:00:01         57.0   23457115   
3         0.40            18.0       0:00:00         63.0   23457115   
4         0.41            45.0       0:00:00         70.0   23457115   
...        ...             ...           ...          ...        ...   
26486     0.40            21.0       0:00:00         34.0   23146908   
26487     0.32            14.0       0:00:00         37.0   23146908   
26488     0.32            26.0       0:00:00         38.0   23146908   
26489     0.40            21.0       0:00:00         59.0   23146908   
26490     0.40            24.0       0:00:00         86.0   23146908   

               reg_no  begin_date  begin_hour    end_date  end_hour  \
0      hiace kcf 954t  2021-07-01           5  2021-07-01         5   
1      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
2      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
3      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
4      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
...               ...         ...         ...         ...       ...   
26486  hiace kcl 589a  2021-08-10          14  2021-08-10        14   
26487  hiace kcl 589a  2021-08-10          14  2021-08-10        14   
26488  hiace kcl 589a  2021-08-10          14  2021-08-10        14   
26489  hiace kcl 589a  2021-08-10          17  2021-08-10        17   
26490  hiace kcl 589a  2021-08-10          19  2021-08-10        19   

         harsh_event    level  
0             Brake:  extreme  
1              Turn:   medium  
2             Brake:   medium  
3             Brake:  extreme  
4              Turn:  extreme  
...              ...      ...  
26486  Acceleration:  extreme  
26487  Acceleration:   medium  
26488         Brake:   medium  
26489         Brake:  extreme  
26490  Acceleration:  extreme  

[26263 rows x 19 columns]

In [8]:
def boxplot_byvio(df,export = True, show = True):
    fig = make_subplots(rows = 1, cols = 3)
    
    fig.add_trace(go.Box(
    y = df.value_g.values,
    x = df.violation.values,
    name='Acceleration value',
    marker_color='#FF851B',
    boxpoints='suspectedoutliers'), row=1, col=1)
    
    fig.add_trace(go.Box(
    y = df.max_speed_kmhr.values,
    x = df.violation.values,
    name='Max speed',
    marker_color= '#3D9970',
    boxpoints='suspectedoutliers'), row=1, col=2)
    
    fig.add_trace(go.Box(
    y = df.distance_km.values,
    x = df.violation.values,
    name='Distance km',
    marker_color= '#FF4136',
    boxpoints='suspectedoutliers'), row=1, col=3)
    
    fig.update_layout(height=800, width=1000,
                      title_text="Boxplot of Max Speed & Acceleration Value & Distance by Violation Types"
                     )
    
    if export:
            file_name = outputs_path + '/' + 'boxplots_byvio_eco_driving.html'
            print('Saving: ' + file_name)
            plotly.offline.plot(fig, filename = file_name, auto_open=False)
    if show:
            fig.show()

boxplot_byvio(eco_data_reprt)

Saving: /Users/ruiwenzhang/Desktop/Kenya/Weekly_report/boxplots_byvio_eco_driving.html


### Duplicates check

In [29]:
drop_rows = (eco_data.violation.str.startswith('Speeding'))
eco_data2 = eco_data[~drop_rows]
eco_data2

violation            begin_datetime  latitude_begin  \
0             Brake: extreme 2021-07-01 05:14:45+03:00       -0.693320   
1               Turn: medium 2021-07-01 08:00:47+03:00       -0.627922   
2              Brake: medium 2021-07-01 08:18:56+03:00       -0.641155   
3             Brake: extreme 2021-07-01 08:33:04+03:00       -0.674540   
4              Turn: extreme 2021-07-01 08:40:59+03:00       -0.710713   
...                      ...                       ...             ...   
26486  Acceleration: extreme 2021-08-10 14:25:29+03:00       -0.517383   
26487   Acceleration: medium 2021-08-10 14:32:00+03:00       -0.501545   
26488          Brake: medium 2021-08-10 14:33:49+03:00       -0.494955   
26489         Brake: extreme 2021-08-10 17:40:24+03:00       -0.452647   
26490  Acceleration: extreme 2021-08-10 19:28:16+03:00       -0.461387   

       longitude_begin              end_datetime  latitude_end  longitude_end  \
0            37.340107 2021-07-01 05:14:45+03:00     -0.693368      37.340037   
1            37.022110 2021-07-01 08:00:48+03:00     -0.627978      37.022003   
2            37.082898 2021-07-01 08:18:57+03:00     -0.641157      37.082925   
3            37.116143 2021-07-01 08:33:04+03:00     -0.674595      37.116137   
4            37.153908 2021-07-01 08:40:59+03:00     -0.710785      37.153978   
...                ...                       ...           ...            ...   
26486        36.940903 2021-08-10 14:25:29+03:00     -0.517332      36.940887   
26487        36.938907 2021-08-10 14:32:00+03:00     -0.501545      36.938920   
26488        36.940573 2021-08-10 14:33:49+03:00     -0.494922      36.940643   
26489        36.958742 2021-08-10 17:40:24+03:00     -0.452693      36.958710   
26490        36.943023 2021-08-10 19:28:16+03:00     -0.461353      36.943063   

       value_g  max_speed_kmhr time_interval  distance_km  reg_no_id  \
0         0.40            34.0       0:00:00         14.0   23672019   
1         0.34            35.0       0:00:01         49.0   23457115   
2         0.32             8.0       0:00:01         57.0   23457115   
3         0.40            18.0       0:00:00         63.0   23457115   
4         0.41            45.0       0:00:00         70.0   23457115   
...        ...             ...           ...          ...        ...   
26486     0.40            21.0       0:00:00         34.0   23146908   
26487     0.32            14.0       0:00:00         37.0   23146908   
26488     0.32            26.0       0:00:00         38.0   23146908   
26489     0.40            21.0       0:00:00         59.0   23146908   
26490     0.40            24.0       0:00:00         86.0   23146908   

               reg_no  begin_date  begin_hour    end_date  end_hour  \
0      hiace kcf 954t  2021-07-01           5  2021-07-01         5   
1      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
2      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
3      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
4      hiace kcw 543m  2021-07-01           8  2021-07-01         8   
...               ...         ...         ...         ...       ...   
26486  hiace kcl 589a  2021-08-10          14  2021-08-10        14   
26487  hiace kcl 589a  2021-08-10          14  2021-08-10        14   
26488  hiace kcl 589a  2021-08-10          14  2021-08-10        14   
26489  hiace kcl 589a  2021-08-10          17  2021-08-10        17   
26490  hiace kcl 589a  2021-08-10          19  2021-08-10        19   

         harsh_event    level  
0             Brake:  extreme  
1              Turn:   medium  
2             Brake:   medium  
3             Brake:  extreme  
4              Turn:  extreme  
...              ...      ...  
26486  Acceleration:  extreme  
26487  Acceleration:   medium  
26488         Brake:   medium  
26489         Brake:  extreme  
26490  Acceleration:  extreme  

[26438 rows x 19 columns]

#### (1) Count the duplicates on all columns

In [25]:
eco_data2.duplicated().sum()

0

#### (2) Count the duplicates on reg_no, begin time, end time, initial location and end location

In [26]:
eco_data2.duplicated(["reg_no","begin_datetime","end_datetime",
                    "latitude_begin","longitude_begin","latitude_end","longitude_end"]).sum()

761

In [27]:
dup_vio_df = eco_data2[eco_data2.duplicated(["reg_no","begin_datetime","end_datetime",
"latitude_begin","longitude_begin","latitude_end","longitude_end"])]

dup_viotype_cnt = dup_vio_df.groupby("violation").apply(lambda x: pd.Series({
    "dup_count": x["reg_no"].count()})).reset_index()
dup_viotype_cnt

violation  dup_count
0          Brake: extreme         19
1            Turn: medium        100
2           Brake: medium          3
3           Turn: extreme         87
4   Acceleration: extreme          6
5    Acceleration: medium         42
6                 Braking        131
7            Acceleration         20
8                    Turn        352
9           Harsh driving          1
10         Speeding: mild          0
11       Speeding: medium          0
12      Speeding: extreme          0

In [28]:
(~eco_data2.duplicated(["reg_no","begin_datetime","end_datetime",
                    "latitude_begin","longitude_begin","latitude_end","longitude_end"])).sum()

25677

In [30]:
nodup_vio_df = eco_data2[(~eco_data2.duplicated(["reg_no","begin_datetime","end_datetime",
                    "latitude_begin","longitude_begin","latitude_end","longitude_end"]))]

nodup_viotype_cnt = nodup_vio_df.groupby("violation").apply(lambda x: pd.Series({
    "nodup_count": x["reg_no"].count()})).reset_index()
nodup_viotype_cnt

violation  nodup_count
0          Brake: extreme         2470
1            Turn: medium          513
2           Brake: medium          683
3           Turn: extreme          217
4   Acceleration: extreme         1318
5    Acceleration: medium          423
6                 Braking        11277
7            Acceleration         4369
8                    Turn         4233
9           Harsh driving          174
10         Speeding: mild            0
11       Speeding: medium            0
12      Speeding: extreme            0

In [36]:
viotype_totcnt = eco_data2.groupby(["violation"]).apply(lambda x: pd.Series({
    "total_count": x["reg_no"].count()})).reset_index()
viotype_totcnt

violation  total_count
0          Brake: extreme         2489
1            Turn: medium          613
2           Brake: medium          686
3           Turn: extreme          304
4   Acceleration: extreme         1324
5    Acceleration: medium          465
6                 Braking        11408
7            Acceleration         4389
8                    Turn         4585
9           Harsh driving          175
10         Speeding: mild            0
11       Speeding: medium            0
12      Speeding: extreme            0

#### Total obs by type that have a duplicate entry and that don't have a duplicate entry

In [39]:
dfs = [viotype_totcnt, nodup_viotype_cnt, dup_viotype_cnt]
reduce(lambda x,y: pd.merge(x,y, on='violation', how='outer'), dfs)


violation  total_count  nodup_count  dup_count
0          Brake: extreme         2489         2470         19
1            Turn: medium          613          513        100
2           Brake: medium          686          683          3
3           Turn: extreme          304          217         87
4   Acceleration: extreme         1324         1318          6
5    Acceleration: medium          465          423         42
6                 Braking        11408        11277        131
7            Acceleration         4389         4369         20
8                    Turn         4585         4233        352
9           Harsh driving          175          174          1
10         Speeding: mild            0            0          0
11       Speeding: medium            0            0          0
12      Speeding: extreme            0            0          0

In [32]:
dup_vio_full = eco_data[eco_data.duplicated(["reg_no","begin_datetime","end_datetime",
                            "latitude_begin","longitude_begin","latitude_end","longitude_end"],
                                         keep = False)].sort_values(["begin_datetime"])
dup_vio_full

violation            begin_datetime  latitude_begin  \
45            Braking 2021-07-01 14:22:28+03:00       -1.264217   
46               Turn 2021-07-01 14:22:28+03:00       -1.264217   
74     Brake: extreme 2021-07-01 14:46:37+03:00       -1.190638   
75            Braking 2021-07-01 14:46:37+03:00       -1.190638   
84               Turn 2021-07-01 14:55:58+03:00       -1.152382   
...               ...                       ...             ...   
25655            Turn 2021-08-10 21:00:51+03:00       -1.841963   
26295            Turn 2021-08-10 21:20:08+03:00       -0.289855   
26294    Acceleration 2021-08-10 21:20:08+03:00       -0.289855   
26310            Turn 2021-08-11 01:42:07+03:00       -1.286327   
26309    Acceleration 2021-08-11 01:42:07+03:00       -1.286327   

       longitude_begin              end_datetime  latitude_end  longitude_end  \
45           36.824513 2021-07-01 14:22:30+03:00     -1.264130      36.824510   
46           36.824513 2021-07-01 14:22:30+03:00     -1.264130      36.824510   
74           36.774200 2021-07-01 14:46:37+03:00     -1.190580      36.774158   
75           36.774200 2021-07-01 14:46:37+03:00     -1.190580      36.774158   
84           36.733680 2021-07-01 14:56:00+03:00     -1.152345      36.733260   
...                ...                       ...           ...            ...   
25655        36.789383 2021-08-10 21:01:02+03:00     -1.841960      36.789883   
26295        36.056730 2021-08-10 21:20:09+03:00     -0.289798      36.056817   
26294        36.056730 2021-08-10 21:20:09+03:00     -0.289798      36.056817   
26310        36.817713 2021-08-11 01:42:09+03:00     -1.286242      36.817908   
26309        36.817713 2021-08-11 01:42:09+03:00     -1.286242      36.817908   

       value_g  max_speed_kmhr time_interval  distance_km  reg_no_id  \
45        0.12            15.0       0:00:02        17.55   23359482   
46        0.11            15.0       0:00:02        17.55   23359482   
74        0.57            28.0       0:00:00        30.00   23359482   
75        0.57            28.0       0:00:00        30.00   23359482   
84        0.32            81.0       0:00:02        36.00   23359482   
...        ...             ...           ...          ...        ...   
25655     0.11            21.0       0:00:11       305.00   23256229   
26295     0.13            23.0       0:00:01       239.00   23359482   
26294     0.12            23.0       0:00:01       239.00   23359482   
26310     0.11            42.0       0:00:02       400.00   23359482   
26309     0.14            42.0       0:00:02       400.00   23359482   

               reg_no  begin_date  begin_hour    end_date  end_hour  \
45      noah kcr 318t  2021-07-01          14  2021-07-01        14   
46      noah kcr 318t  2021-07-01          14  2021-07-01        14   
74      noah kcr 318t  2021-07-01          14  2021-07-01        14   
75      noah kcr 318t  2021-07-01          14  2021-07-01        14   
84      noah kcr 318t  2021-07-01          14  2021-07-01        14   
...               ...         ...         ...         ...       ...   
25655  hiace kcm 320j  2021-08-10          21  2021-08-10        21   
26295   noah kcr 318t  2021-08-10          21  2021-08-10        21   
26294   noah kcr 318t  2021-08-10          21  2021-08-10        21   
26310   noah kcr 318t  2021-08-11           1  2021-08-11         1   
26309   noah kcr 318t  2021-08-11           1  2021-08-11         1   

        harsh_event    level  
45          Braking     None  
46             Turn     None  
74           Brake:  extreme  
75          Braking     None  
84             Turn     None  
...             ...      ...  
25655          Turn     None  
26295          Turn     None  
26294  Acceleration     None  
26310          Turn     None  
26309  Acceleration     None  

[1468 rows x 19 columns]

In [63]:
dup_vio_full.groupby(["begin_datetime",'violation']).size().to_frame('size')

size
begin_datetime            violation           
2021-07-01 14:22:28+03:00 Braking            1
                          Turn               1
2021-07-01 14:46:37+03:00 Brake: extreme     1
                          Braking            1
2021-07-01 14:55:58+03:00 Turn: medium       1
...                                        ...
2021-08-10 21:00:51+03:00 Turn               1
2021-08-10 21:20:08+03:00 Acceleration       1
                          Turn               1
2021-08-11 01:42:07+03:00 Acceleration       1
                          Turn               1

[1468 rows x 1 columns]

In [64]:
dup_vio_full.violation.unique()

[Braking, Turn, Brake: extreme, Turn: medium, Turn: extreme, Acceleration: medium, Brake: medium, Acceleration, Acceleration: extreme, Harsh driving]
Categories (10, object): [Braking, Turn, Brake: extreme, Turn: medium, ..., Brake: medium, Acceleration, Acceleration: extreme, Harsh driving]

In [34]:
dup_vio_full.to_csv("duplicated_vio_full.csv", index = False)

#### (3) Count the duplicates on reg_no and begin_time, to check if the begin time is the same but the initial location is different

In [66]:
eco_data2.duplicated(["reg_no","begin_datetime"]).sum()

1492

In [70]:
dup_vio_df2 = eco_data2[eco_data2.duplicated(["reg_no","begin_datetime"])]

dup_viotype_cnt2 = dup_vio_df2.groupby("violation").apply(lambda x: pd.Series({
    "dup_count": x["reg_no"].count()})).reset_index()
dup_viotype_cnt2

violation  dup_count
0          Brake: extreme        222
1            Turn: medium        105
2           Brake: medium         31
3           Turn: extreme         95
4   Acceleration: extreme         51
5    Acceleration: medium         49
6                 Braking        292
7            Acceleration         80
8                    Turn        462
9           Harsh driving        105
10         Speeding: mild          0
11       Speeding: medium          0
12      Speeding: extreme          0

In [67]:
(~eco_data2.duplicated(["reg_no","begin_datetime"])).sum()

24946

In [71]:
nodup_vio_df2 = eco_data2[(~eco_data2.duplicated(["reg_no","begin_datetime"]))]

nodup_viotype_cnt2 = nodup_vio_df2.groupby("violation").apply(lambda x: pd.Series({
    "nodup_count": x["reg_no"].count()})).reset_index()
nodup_viotype_cnt2

violation  nodup_count
0          Brake: extreme         2267
1            Turn: medium          508
2           Brake: medium          655
3           Turn: extreme          209
4   Acceleration: extreme         1273
5    Acceleration: medium          416
6                 Braking        11116
7            Acceleration         4309
8                    Turn         4123
9           Harsh driving           70
10         Speeding: mild            0
11       Speeding: medium            0
12      Speeding: extreme            0

In [73]:
dfs = [viotype_totcnt, nodup_viotype_cnt2, dup_viotype_cnt2]
reduce(lambda x,y: pd.merge(x,y, on='violation', how='outer'), dfs)

violation  total_count  nodup_count  dup_count
0          Brake: extreme         2489         2267        222
1            Turn: medium          613          508        105
2           Brake: medium          686          655         31
3           Turn: extreme          304          209         95
4   Acceleration: extreme         1324         1273         51
5    Acceleration: medium          465          416         49
6                 Braking        11408        11116        292
7            Acceleration         4389         4309         80
8                    Turn         4585         4123        462
9           Harsh driving          175           70        105
10         Speeding: mild            0            0          0
11       Speeding: medium            0            0          0
12      Speeding: extreme            0            0          0

In [72]:
dup_vio_df2_full = eco_data2[eco_data2.duplicated(["reg_no","begin_datetime"],
                                         keep = False)].sort_values(["begin_datetime"])
dup_vio_df2_full

violation            begin_datetime  latitude_begin  \
45                   Braking 2021-07-01 14:22:28+03:00       -1.264217   
46                      Turn 2021-07-01 14:22:28+03:00       -1.264217   
74            Brake: extreme 2021-07-01 14:46:37+03:00       -1.190638   
75                   Braking 2021-07-01 14:46:37+03:00       -1.190638   
84                      Turn 2021-07-01 14:55:58+03:00       -1.152382   
...                      ...                       ...             ...   
26294           Acceleration 2021-08-10 21:20:08+03:00       -0.289855   
26310                   Turn 2021-08-11 01:42:07+03:00       -1.286327   
26309           Acceleration 2021-08-11 01:42:07+03:00       -1.286327   
25675         Brake: extreme 2021-08-11 02:00:56+03:00       -0.350293   
25674  Acceleration: extreme 2021-08-11 02:00:56+03:00       -0.350475   

       longitude_begin              end_datetime  latitude_end  longitude_end  \
45           36.824513 2021-07-01 14:22:30+03:00     -1.264130      36.824510   
46           36.824513 2021-07-01 14:22:30+03:00     -1.264130      36.824510   
74           36.774200 2021-07-01 14:46:37+03:00     -1.190580      36.774158   
75           36.774200 2021-07-01 14:46:37+03:00     -1.190580      36.774158   
84           36.733680 2021-07-01 14:56:00+03:00     -1.152345      36.733260   
...                ...                       ...           ...            ...   
26294        36.056730 2021-08-10 21:20:09+03:00     -0.289798      36.056817   
26310        36.817713 2021-08-11 01:42:09+03:00     -1.286242      36.817908   
26309        36.817713 2021-08-11 01:42:09+03:00     -1.286242      36.817908   
25675        37.620633 2021-08-11 02:00:59+03:00     -0.350715      37.620415   
25674        37.620527 2021-08-11 02:00:58+03:00     -0.350595      37.620488   

       value_g  max_speed_kmhr time_interval  distance_km  reg_no_id  \
45        0.12            15.0       0:00:02        17.55   23359482   
46        0.11            15.0       0:00:02        17.55   23359482   
74        0.57            28.0       0:00:00        30.00   23359482   
75        0.57            28.0       0:00:00        30.00   23359482   
84        0.32            81.0       0:00:02        36.00   23359482   
...        ...             ...           ...          ...        ...   
26294     0.12            23.0       0:00:01       239.00   23359482   
26310     0.11            42.0       0:00:02       400.00   23359482   
26309     0.14            42.0       0:00:02       400.00   23359482   
25675     0.63            64.0       0:00:03       248.00   23672019   
25674     0.85            93.0       0:00:02       248.00   23672019   

               reg_no  begin_date  begin_hour    end_date  end_hour  \
45      noah kcr 318t  2021-07-01          14  2021-07-01        14   
46      noah kcr 318t  2021-07-01          14  2021-07-01        14   
74      noah kcr 318t  2021-07-01          14  2021-07-01        14   
75      noah kcr 318t  2021-07-01          14  2021-07-01        14   
84      noah kcr 318t  2021-07-01          14  2021-07-01        14   
...               ...         ...         ...         ...       ...   
26294   noah kcr 318t  2021-08-10          21  2021-08-10        21   
26310   noah kcr 318t  2021-08-11           1  2021-08-11         1   
26309   noah kcr 318t  2021-08-11           1  2021-08-11         1   
25675  hiace kcf 954t  2021-08-11           2  2021-08-11         2   
25674  hiace kcf 954t  2021-08-11           2  2021-08-11         2   

         harsh_event    level  
45           Braking     None  
46              Turn     None  
74            Brake:  extreme  
75           Braking     None  
84              Turn     None  
...              ...      ...  
26294   Acceleration     None  
26310           Turn     None  
26309   Acceleration     None  
25675         Brake:  extreme  
25674  Acceleration:  extreme  

[2843 rows x 19 columns]

In [74]:
dup_vio_df2_full.to_csv("duplicated_vio_full2.csv", index = False)